In [1]:
## 因子计算分析
 
import datetime

from tqsdk import TqApi, TqAuth
from tqsdk.tafunc import get_t, get_bs_price

import numpy as np
import pandas as pd
import plotly.express as px

pd.options.display.max_rows= None
pd.options.display.max_columns = None
pd.options.display.width = 0
pd.options.display.float_format = '{:.6f}'.format

在使用天勤量化之前，默认您已经知晓并同意以下免责条款，如果不同意请立即停止使用：https://www.shinnytech.com/blog/disclaimer/


In [2]:
# 标准 BS 定价模型假设波动律为常量, 但是波动率实际和时间相关, 这里扩展 BS 定价模型引入时间相关波动率并与标准模型进行对比
api = TqApi(auth=TqAuth('快期账户', '快期密码'))
quote = api.get_quote('CFFEX.IO2405-C-3550')
underlying = quote.underlying_symbol
exp = datetime.datetime.fromtimestamp(quote.expire_datetime)

2024-06-26 16:40:45 -     INFO - 通知 : 与 wss://api.shinnytech.com/t/nfmd/front/mobile 的网络连接已建立


In [3]:
# 获取沪深300指数过去一年的5分钟现数据，用来分析波动率
csi = api.get_kline_data_series(symbol=underlying, duration_seconds=300, start_dt=exp-datetime.timedelta(days=365), end_dt=exp)
# 将 unix time 转换成 pandas.Datetime 并获得周几及时间信息
csi["dt"] = pd.to_datetime(csi["datetime"], utc=True).dt.tz_convert('Asia/Shanghai')
csi["time"] = csi["dt"].dt.time
csi["week"] = csi["dt"].dt.weekday+1
# p 为每五分钟的波动率, 不计算跨交易时段的波动, 用来分析波动率的周期性
csi["p"] = np.log(csi["close"]/csi["open"])

In [4]:
# 可以看到周一到周五的波动率有显著性的差异
px.bar(csi.groupby("week").std(numeric_only=True), y="p")


In [5]:
# 每天不同时间段的波动率也有显著性的差异
# 早上及下午开盘的波动率显著偏高
# 注意这里的波动率是收盘价对比开盘价, 而不是收盘价对比上个收盘价, 因此 9:30 开盘的高波动率只包含集合竞价之后的价格波动, 不包含相对昨天收盘的波动
px.bar(csi.groupby("time").std(numeric_only=True), y="p")

In [6]:
# 按周一~五绘制出不同时段的波动率, 可以观察到周一的 9:30 又显著高于周二~五
px.line(csi.groupby(["week","time"]).std(numeric_only=True).reset_index(), x="time", y="p", color="week")

In [7]:
# 上述信息验证了波动率实际和时间相关的假设, 接下来基于该假设计算改进版的 BS 定价
# Tσ² = ∫σ²(dt)
# 其中 T 是距离到期时间, 按照波动率的周期性积分出改进版波动率
# 这里计算的 r 是使用当前周期的收盘价对比上一周期的收盘价, 使得积分的结果能够完整的覆盖 T
csi["r"] = np.log(csi["close"].shift(1)/csi["close"])
# 得到周一~五不同时间段的周期性收益率方差
csiv = csi.groupby(["week","time"]).var(numeric_only=True).reset_index()[["week", "time", "r"]]

In [8]:
# 只关注期权最后一周的行情数据
serial = api.get_kline_serial(symbol=[underlying, quote.instrument_id], duration_seconds=300, data_length=48*5)
serial["dt"] = pd.to_datetime(serial["datetime"], utc=True).dt.tz_convert('Asia/Shanghai')
serial["time"] = serial["dt"].dt.time
serial["week"] = serial["dt"].dt.weekday+1
# 最后一个交易日使用最后两小时的算数平均数作为交割结算价
serial["close_avg"] = serial["close"]
serial.iloc[-24:, serial.columns.get_loc("close_avg")] = serial["close"].iloc[-24:].expanding().mean()

In [9]:
# 将 csi 周期性收益率方差 join 期权价量信息, 计算出改进版波动率
serial = serial.merge(csiv, on=["week", "time"])

In [10]:
# v 为年化后的改进版波动率
serial["v"] = np.sqrt(serial["r"].iloc[::-1].expanding().mean()*48*250)

In [11]:
# 无风险利率 1.5%
rf = 0.015
# 距离到期的时间序列
t = get_t(serial, quote.expire_datetime)
# 行权价格的折现, 用于计算时间价值
serial["present_k"] = quote.strike_price * np.exp(-rf * t)
serial["time_value"] = (serial["close_avg"] - serial["present_k"]) - serial["close1"]
# 计算标准和改进版 BS 模型价格, 以及和实际期权价格的差
# 最后两小时使用算数平均作为交割结算价导致不能简单的使用波动率来估计交割结算价的变化, 因此跳过最后两小时
# v 为标准 BS 模型所用到的波动率
v = np.sqrt(np.var(csi["r"]) * 250*48)
serial["bs"] = get_bs_price(serial["close"].iloc[:-24], k=quote.strike_price, r=rf, v=v, t=t.iloc[:-24], option_class=quote.option_class)
serial["bs_diff"] = serial["bs"] - serial["close1"]
serial["tdbs"] = get_bs_price(serial["close"].iloc[:-24], k=quote.strike_price, r=rf, v=serial["v"].iloc[:-24], t=t.iloc[:-24], option_class=quote.option_class)
serial["tdbs_diff"] = serial["tdbs"] - serial["close1"]

In [12]:
# 计算结果
serial[["dt", "close_avg", "time_value", "close1", "bs", "bs_diff", "tdbs", "tdbs_diff"]]

dt   close_avg  time_value     close1         bs  \
0   2024-05-13 09:30:00+08:00 3642.430000    1.654996  91.400000  94.055250   
1   2024-05-13 09:35:00+08:00 3642.540000    0.764482  92.400000  94.157842   
2   2024-05-13 09:40:00+08:00 3640.660000    0.083969  91.200000  92.360068   
3   2024-05-13 09:45:00+08:00 3642.880000   -0.096545  93.600000  94.477975   
4   2024-05-13 09:50:00+08:00 3644.590000   -0.387058  95.600000  96.114526   
5   2024-05-13 09:55:00+08:00 3644.780000    0.602428  94.800000  96.294486   
6   2024-05-13 10:00:00+08:00 3643.400000    0.021915  94.000000  94.968284   
7   2024-05-13 10:05:00+08:00 3649.690000   -1.288599 101.600000 101.022761   
8   2024-05-13 10:10:00+08:00 3653.490000    0.710888 103.400000 104.706017   
9   2024-05-13 10:15:00+08:00 3658.290000   -0.289626 109.200000 109.383127   
10  2024-05-13 10:20:00+08:00 3659.020000    1.039861 108.600000 110.095092   
11  2024-05-13 10:25:00+08:00 3658.620000    2.239347 107.000000 109.702235   
12  2024-05-13 10:30:00+08:00 3660.600000    1.818833 109.400000 111.638249   
13  2024-05-13 10:35:00+08:00 3659.830000    1.248320 109.200000 110.882588   
14  2024-05-13 10:40:00+08:00 3660.470000    1.487806 109.600000 111.507632   
15  2024-05-13 10:45:00+08:00 3667.410000   -0.172707 118.200000 118.323862   
16  2024-05-13 10:50:00+08:00 3669.310000   -1.873221 121.800000 120.195245   
17  2024-05-13 10:55:00+08:00 3667.370000    0.986266 117.000000 118.281704   
18  2024-05-13 11:00:00+08:00 3663.970000    0.585752 114.000000 114.935195   
19  2024-05-13 11:05:00+08:00 3663.260000    1.475239 112.400000 114.236226   
20  2024-05-13 11:10:00+08:00 3659.890000    1.104725 109.400000 110.929702   
21  2024-05-13 11:15:00+08:00 3661.100000    1.714212 110.000000 112.113643   
22  2024-05-13 11:20:00+08:00 3663.910000    1.123698 113.400000 114.870255   
23  2024-05-13 11:25:00+08:00 3665.520000    1.133185 115.000000 116.451949   
24  2024-05-13 13:00:00+08:00 3666.680000    0.883428 116.400000 117.567562   
25  2024-05-13 13:05:00+08:00 3669.440000    0.842915 119.200000 120.288497   
26  2024-05-13 13:10:00+08:00 3666.950000    0.952401 116.600000 117.830932   
27  2024-05-13 13:15:00+08:00 3664.050000    1.251888 113.400000 114.973967   
28  2024-05-13 13:20:00+08:00 3668.220000    0.821374 118.000000 119.080619   
29  2024-05-13 13:25:00+08:00 3671.950000    0.750861 121.800000 122.763406   
30  2024-05-13 13:30:00+08:00 3672.090000    0.490347 122.200000 122.900642   
31  2024-05-13 13:35:00+08:00 3670.360000    1.359834 119.600000 121.189497   
32  2024-05-13 13:40:00+08:00 3669.600000    1.399320 118.800000 120.437575   
33  2024-05-13 13:45:00+08:00 3669.570000   -0.231193 120.400000 120.406686   
34  2024-05-13 13:50:00+08:00 3670.170000    0.568293 120.200000 120.998062   
35  2024-05-13 13:55:00+08:00 3670.580000   -1.622220 122.800000 121.401920   
36  2024-05-13 14:00:00+08:00 3673.590000    0.787266 123.400000 124.377621   
37  2024-05-13 14:05:00+08:00 3669.120000    0.316752 119.400000 119.957257   
38  2024-05-13 14:10:00+08:00 3665.720000    2.316239 114.000000 116.602395   
39  2024-05-13 14:15:00+08:00 3662.720000    1.715725 111.600000 113.648407   
40  2024-05-13 14:20:00+08:00 3660.120000   -0.284788 111.000000 111.093480   
41  2024-05-13 14:25:00+08:00 3659.050000    0.244698 109.400000 110.042649   
42  2024-05-13 14:30:00+08:00 3658.900000    1.094185 108.400000 109.894002   
43  2024-05-13 14:35:00+08:00 3662.210000    0.803671 112.000000 113.141110   
44  2024-05-13 14:40:00+08:00 3664.110000    0.703158 114.000000 115.008462   
45  2024-05-13 14:45:00+08:00 3662.850000   -0.757356 114.200000 113.767335   
46  2024-05-13 14:50:00+08:00 3663.660000    0.452131 113.800000 114.562703   
47  2024-05-13 14:55:00+08:00 3664.690000    1.881617 113.400000 115.575260   
48  2024-05-14 09:30:00+08:00 3675.380000   -0.142898 126.000000 125.923052   
49  2024-05-14 09:35:00+08:00 3669.180000    0.856588 118.800000 119.754387  

In [13]:
# 绘制出时间价值(time_value), 标准 BS 定价与期权价格的差(bs_diff), 改进版 BS 定价与期权价格的差(tdbs_diff)
px.line(serial, x="dt", y=["time_value", "bs_diff", "tdbs_diff"])

In [14]:
# 残差均值
serial[["bs_diff", "tdbs_diff"]].mean()

bs_diff     0.873137
tdbs_diff   0.793846
dtype: float64

In [15]:
# 标准模型的残差标准差
np.log(serial["bs"]/serial["close1"]).std()

0.016289936725434342

In [16]:
# 改进模型的残差标准差
np.log(serial["tdbs"]/serial["close1"]).std()

0.016233962768335282

In [17]:
api.close()